# TensorFlow Basics

### We need to install the tensorflow package using pip, and we can furthermore install tensorflow-metal to utilize non-NVIDIA GPUs

In [1]:
!pip install tensorflow
!pip install tensorflow-metal

DEPRECATION: Loading egg at /Users/andreas/anaconda3/lib/python3.12/site-packages/Pylians-0.12-py3.12-macosx-11.1-arm64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330
DEPRECATION: Loading egg at /Users/andreas/anaconda3/lib/python3.12/site-packages/Pylians-0.12-py3.12-macosx-11.1-arm64.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [2]:
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np
from time import time

In [3]:
# warm up tensorflow by creating a constant
a = tf.constant(1)

2025-09-30 15:43:59.292950: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M4 Pro
2025-09-30 15:43:59.292987: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 48.00 GB
2025-09-30 15:43:59.292992: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 18.00 GB
2025-09-30 15:43:59.293019: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2025-09-30 15:43:59.293034: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


## Test operations between scalars and tensors

In [4]:
# create tensorflow constants and try out operations
a = tf.constant(2)
b = tf.constant(3)
c = a + b
print(c)

a = tf.constant([[1, 2],
                 [3, 4]])
b = tf.constant([[5, 6],
                 [7, 8]])
c = a + b
print(c)

tf.Tensor(5, shape=(), dtype=int32)
tf.Tensor(
[[ 6  8]
 [10 12]], shape=(2, 2), dtype=int32)


## Test TensorFlow's speed by performing a very large matrix multiplication

In [5]:
# test tensorflow speed vs numpy speed
N = 10_000
a = np.random.rand(N, N).astype(np.float32)
b = np.random.rand(N, N).astype(np.float32)

In [6]:
# tensorflow
with tf.device('/CPU:0'):
    a_tf = tf.constant(a)
    b_tf = tf.constant(b)
    # warm up (needed for fair timing)
    _ = tf.matmul(a_tf, b_tf)
    start = time()
    c_tf = tf.matmul(a_tf, b_tf)
    tf_time = time() - start
# numpy
start = time()
c_np = np.matmul(a, b)
np_time = time() - start
# print results
print(f"TensorFlow time: {tf_time:.4f} seconds")
print(f"Numpy time: {np_time:.4f} seconds")

TensorFlow time: 2.1343 seconds
Numpy time: 2.5690 seconds


## We can see that TensorFlow is faster than NumPy on a CPU, but let's try the GPU (if available) as well

In [7]:
# now use your GPU if available
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))
if len(tf.config.list_physical_devices('GPU')) > 0:
    with tf.device('/GPU:0'):
        a_tf_gpu = tf.constant(a)
        b_tf_gpu = tf.constant(b)
        # warm up
        _ = tf.matmul(a_tf_gpu, b_tf_gpu)
        # tensorflow on GPU
        start = time()
        c_tf_gpu = tf.matmul(a_tf_gpu, b_tf_gpu)
        tf_gpu_time = time() - start
    print(f"TensorFlow on GPU time: {tf_gpu_time:.4f} seconds")

Num GPUs Available:  1
TensorFlow on GPU time: 0.0005 seconds


## This is an insane speed-up! Let's check that the results are consistent

In [8]:
# check if results are the same
print("Result by Numpy:\n", c_np, "\n")
print("Result by TensorFlow:\n", c_tf.numpy(), "\n")
print("Result by TensorFlow on GPU:\n", c_tf_gpu.numpy() if len(tf.config.list_physical_devices('GPU')) > 0 else "N/A", "\n")

print("Results are the same:", np.allclose(c_np, c_tf.numpy()) and (np.allclose(c_np, c_tf_gpu.numpy()) if len(tf.config.list_physical_devices('GPU')) > 0 else True))

Result by Numpy:
 [[2504.091  2506.2424 2498.9204 ... 2503.06   2516.3018 2530.2786]
 [2470.415  2478.6516 2478.1443 ... 2485.5725 2478.0344 2488.7886]
 [2452.968  2471.3296 2484.2075 ... 2474.1973 2477.2236 2499.5105]
 ...
 [2479.1218 2477.7615 2488.4922 ... 2494.186  2492.8184 2490.0906]
 [2480.6992 2499.7612 2503.5312 ... 2487.1755 2495.6897 2526.1846]
 [2460.9973 2471.0679 2471.9412 ... 2482.3337 2462.5952 2482.8706]] 

Result by TensorFlow:
 [[2504.091  2506.242  2498.9202 ... 2503.0605 2516.3018 2530.278 ]
 [2470.414  2478.6514 2478.1443 ... 2485.572  2478.0347 2488.788 ]
 [2452.9685 2471.3296 2484.2075 ... 2474.1978 2477.224  2499.5107]
 ...
 [2479.1216 2477.7612 2488.4922 ... 2494.1863 2492.8184 2490.09  ]
 [2480.6992 2499.7612 2503.5312 ... 2487.1753 2495.6907 2526.184 ]
 [2460.9978 2471.068  2471.9407 ... 2482.3333 2462.595  2482.8696]] 

Result by TensorFlow on GPU:
 [[2504.0837 2506.2385 2498.9153 ... 2503.0554 2516.3108 2530.2622]
 [2470.4128 2478.651  2478.1438 ... 2485.5

## There is a lot to gain from utilizing TensorFlow and GPUs!